In [1]:
import numpy as np
import pandas as pd

In [2]:
training_data = np.load(f'../fashion_train.npy')
test_data = np.load(f'../fashion_test.npy')

In [3]:
df = pd.DataFrame(training_data)
dftest = pd.DataFrame(test_data)


dftest_2classes =  dftest#[dftest.iloc[:, -1] < 2]
df_2classes = df#[df.iloc[:, -1] < 2]
df_2classes.head()

0    1    2    3    4    5    6    7    8    9    ...  775  776  777  778  \
0    0    0    0    0    0    3    0    0    0   41  ...   63   78   11    0   
1    0    0    0    0    0    0    0    0    0    0  ...   32    0    0    0   
2    0    0    0    0    0    1    1    0    0    0  ...  168  119    0    0   
3    0    0    0    0    0    0    0    0    0   98  ...   21    0    0    0   
4    0    0    0    0    0    0    0    2    0    0  ...   88  128   46    0   

   779  780  781  782  783  784  
0    2    0    0    0    0    0  
1    0    0    0    0    0    1  
2    0    0    0    0    0    0  
3    0    0    0    0    0    3  
4    0    0    0    0    0    4  

[5 rows x 785 columns]

### Create subset for fast testing

In [4]:
# Split data: 80% sample
df_2classes_subset = df_2classes.sample(frac=1, random_state=1)

# Separate the last column to keep it unchanged
#last_column = df_2classes_subset.iloc[:, -1]

# Apply transformation to all columns except the last one
#df_2classes_subset.iloc[:, :-1] = (df_2classes_subset.iloc[:, :-1] / 255 * 10).round().astype(int)

# Concatenate the transformed data and the last column
#df_2classes_subset = pd.concat([df_2classes_subset.iloc[:, :-1], last_column], axis=1)

#df_2classes_subset


In [94]:
# Split data: 80% sample
test_data_trans = df_2classes.sample(frac=1, random_state=1)

# Separate the last column to keep it unchanged
#last_column = test_data_trans.iloc[:, -1]

# Apply transformation to all columns except the last one
#test_data_trans.iloc[:, :-1] = (test_data_trans.iloc[:, :-1] / 255 * 10).round().astype(int)

# Concatenate the transformed data and the last column
#test_data_trans = pd.concat([test_data_trans.iloc[:, :-1], last_column], axis=1)

#test_data_trans


### Decision tree (Needs water)

In [95]:
import numpy as np

def find_best_split(data):
    best_i = None
    best_column = None
    current_min = 2  # Gini ranges from 0 to 1; initialize with a high value.
    best_split1, best_split2 = None, None
    split_info = None    

    n = len(data)

    for column in data.columns[:-1]:
        # Sort data by the column for efficient split calculations
        sorted_data = data.sort_values(by=column)
        values = sorted_data[column].values
        labels = sorted_data[data.columns[-1]].values

        # Initialize running totals for calculating Gini efficiently
        left_counts = np.zeros(5, dtype=float)
        right_counts = np.bincount(labels, minlength=5).astype(float)
        total_right = len(labels)

        for i in range(len(values) - 1):
            label = labels[i]
            left_counts[label] += 1
            right_counts[label] -= 1

            total_left = i + 1
            total_right -= 1

            # Only consider unique values for splits
            if values[i] == values[i + 1]:
                continue

            gini_left = 1.0 - np.sum((left_counts / total_left) ** 2)
            gini_right = 1.0 - np.sum((right_counts / total_right) ** 2)
            weighted_gini = (gini_left * total_left + gini_right * total_right) / n

            if weighted_gini < current_min:
                best_i = i
                best_column = column
                current_min = weighted_gini
                split_info = [current_min, column, values[i]]

    # Sort the data again by the best column
    sorted_data = data.sort_values(by=best_column)

    # Now split the data into two parts based on best_i
    best_split1 = sorted_data.iloc[:best_i + 1]  # Use iloc to select all columns up to best_i
    best_split2 = sorted_data.iloc[best_i + 1:]  # Use iloc to select all columns after best_i

    # Get the majority class of each split
    Split_majoritys = [
        best_split1[data.columns[-1]].mode().iloc[0],
        best_split2[data.columns[-1]].mode().iloc[0]
    ]

    return split_info, Split_majoritys


In [96]:
k = 10
splits = {i: [] for i in range(k)}

def split_data(data,level):

    if  isinstance(data, str) and data == "deadleaf": #leaf detection
      splits[level].append(("deadleaf")) 
      if level + 1 < k:
            split_data("deadleaf", level + 1)
            split_data("deadleaf", level + 1)

    elif data.iloc[:, -1].nunique() == 1: #leaf detection
      majority=(data[data.columns[-1]].mode().iloc[0])
      splits[level].append(("leaf",majority)) 
      if level + 1 < k:
            split_data("deadleaf", level + 1)
            split_data("deadleaf", level + 1)

    else:
      result=find_best_split(data)
      gini,column,value=result[0]
      left_majority,right_majority=result[1]
      df1 = data[data[column] > value]
      df2 = data[data[column] <= value]
      # Update splits dictionary
      splits[level].append((gini,column,value,left_majority,right_majority))
      #splits[level].append((len(data), split_index))
      # Recursive splitting until level reaches `k`
      if level + 1 < k:
          split_data(df2, level + 1)
          split_data(df1, level + 1)


split_data(df_2classes_subset,0)


In [97]:
print(splits[0])
print(splits[1])
print(splits[2])
print(splits[3])
print(splits[4])
print(splits[5])
print(splits[6])
print(splits[7])
print(splits[8])
print(splits[9])


splits2=splits




[(0.6532301649304488, 546, 13, 1, 0)]
[(0.08168711300568471, 549, 44, 0, 1), (0.6222149379123547, 621, 9, 3, 2)]
[(0.6530261408949932, 649, 3, 0, 2), (0.027535783586052853, 602, 57, 1, 1), (0.4778575957622566, 173, 8, 3, 0), (0.41033111084956597, 46, 4, 4, 2)]
[(0.501987083954297, 631, 57, 0, 1), (0.4522222222222223, 778, 0, 4, 2), (0.014006815879156214, 347, 14, 0, 1), (0.5079365079365079, 265, 224, 4, 1), (0.4611369994466137, 623, 8, 3, 3), (0.38387727443895214, 425, 19, 0, 4), (0.3003390218105937, 770, 6, 4, 4), (0.37659857153676296, 769, 10, 2, 2)]
[(0.1875, 428, 165, 0, 4), (0.3604465709728868, 490, 7, 1, 3), (0.09523809523809523, 512, 35, 0, 4), (0.3402777777777778, 21, 1, 2, 4), (0.26666666666666666, 9, 0, 0, 4), (0.009462525020386973, 518, 60, 1, 3), (0.4666666666666667, 35, 50, 4, 0), ('leaf', 1), (0.2913562266355332, 714, 70, 1, 3), (0.575532862199598, 232, 4, 3, 0), (0.3034531019041904, 38, 24, 4, 0), (0.5712311516155759, 275, 3, 3, 4), (0.4476942261034216, 92, 35, 2, 4), (0

In [98]:
def predict(row):
    lastcheck=0
    depth=len(splits)-1
    currentclass=None
    for i in range(depth):
        #print(lastcheck)
        if splits[i][lastcheck][0]=="leaf":
            return currentclass#splits[i][lastcheck][1]
    
        if splits[i][lastcheck]=="deadleaf":
            print("error unreachable node reached")

        elif row[splits[i][lastcheck][1]] <= splits[i][lastcheck][2]:
            #print(row[splits[i][lastcheck][1]],splits[i][lastcheck][2]) 
            currentclass = splits[i][lastcheck][4]  # Class for right child
            #print(currentclass)
            lastcheck=2*lastcheck

        else:
            currentclass = splits[i][lastcheck][3]  # Class for left child
            #print(currentclass)
            lastcheck=2*lastcheck+1
            
   # print("we did it")        
    return currentclass



In [99]:
predict(list(test_data_trans.iloc[3]))

0

In [100]:
from sklearn.metrics import confusion_matrix, accuracy_score

# Generate predictions, passing each row in test_data_trans to predict
predictions = []

for k in range(test_data_trans.shape[0]):
    predictions.append(predict(list(test_data_trans.iloc[k]))) 
    
predictions

# Assuming the last element in each row is the true label
true_labels  = list(test_data_trans.iloc[:, -1])

print(predictions)
print(true_labels)

# Calculate the confusion matrix and accuracy
conf_matrix = confusion_matrix(true_labels, predictions)
accuracy = accuracy_score(true_labels, predictions)

print("Confusion Matrix:")
print(conf_matrix)
print(f"Accuracy: {accuracy * 100:.2f}%")


[4, 3, 3, 0, 4, 0, 1, 1, 1, 4, 4, 4, 4, 3, 4, 4, 0, 1, 3, 1, 4, 3, 4, 1, 0, 1, 1, 2, 4, 3, 0, 4, 4, 0, 1, 4, 1, 1, 4, 3, 4, 4, 4, 3, 0, 3, 0, 4, 4, 3, 2, 3, 4, 1, 3, 0, 0, 4, 0, 0, 1, 3, 3, 4, 1, 0, 0, 3, 4, 3, 4, 4, 4, 1, 1, 4, 4, 0, 3, 4, 4, 1, 1, 1, 4, 0, 1, 0, 4, 4, 4, 2, 1, 0, 1, 3, 0, 1, 4, 4, 1, 3, 4, 0, 4, 4, 3, 1, 4, 3, 3, 0, 0, 4, 1, 3, 3, 4, 4, 3, 4, 3, 3, 2, 0, 3, 3, 1, 2, 3, 1, 0, 1, 0, 3, 4, 3, 4, 2, 0, 1, 0, 0, 3, 4, 4, 1, 0, 4, 0, 1, 4, 0, 0, 4, 4, 1, 2, 0, 4, 0, 3, 4, 0, 1, 4, 1, 4, 3, 0, 4, 4, 3, 1, 0, 4, 1, 2, 4, 0, 1, 1, 2, 0, 0, 3, 4, 2, 0, 3, 4, 0, 3, 1, 1, 4, 0, 3, 1, 3, 0, 4, 1, 1, 3, 4, 4, 4, 4, 3, 4, 1, 0, 3, 4, 0, 3, 0, 4, 0, 3, 3, 4, 4, 4, 4, 0, 4, 1, 0, 4, 4, 1, 2, 2, 0, 3, 0, 1, 4, 3, 4, 4, 0, 3, 4, 3, 1, 0, 3, 1, 1, 4, 0, 3, 2, 2, 0, 4, 2, 3, 4, 0, 4, 4, 0, 3, 4, 0, 1, 3, 4, 1, 4, 0, 0, 1, 3, 1, 0, 3, 3, 0, 4, 0, 1, 1, 4, 3, 0, 1, 3, 0, 0, 2, 2, 4, 4, 0, 4, 3, 4, 3, 1, 3, 2, 0, 4, 0, 4, 4, 4, 3, 4, 4, 1, 4, 0, 3, 1, 4, 0, 3, 1, 4, 3, 0, 4, 1, 1, 3, 0, 4, 

In [101]:
# Initialize a counter to store the frequency of each leaf
from collections import Counter
leaf_values = []

# Iterate through all splits and collect leaf values
for sublist in range(len(splits)):
    for item in splits[sublist]:
        if isinstance(item, tuple) and item[0] == 'leaf':  # Check if it is a leaf
            leaf_values.append(item[1])  # Append the leaf value (e.g., 1, 4, etc.)

# Count occurrences of each leaf value using Counter
leaf_counts = Counter(leaf_values)

# Print the leaf counts
print("Leaf values and their counts:")
for leaf, count in leaf_counts.items():
    print(f"Leaf: {leaf}, Count: {count}")

Leaf values and their counts:
Leaf: 1, Count: 11
Leaf: 4, Count: 48
Leaf: 0, Count: 29
Leaf: 2, Count: 29
Leaf: 3, Count: 23


In [234]:
def test2(data):
    for column in data.columns[:-1]:
        # Slice data to include the current column and the last column
        sliced_data = data[[column, data.columns[-1]]]

        # Group by the first column and count occurrences of each class in the second column
        grouped = sliced_data.groupby(sliced_data.columns[0])[sliced_data.columns[1]].value_counts().unstack(fill_value=0)

        # Ensure only classes 0 to 4 are present and in order
        grouped = grouped.reindex(columns=range(5), fill_value=0)

        # Convert to a dictionary with lists as values
        result_dict = grouped.to_dict(orient="index")

        print(result_dict)  # Debugging output
        
      # Remove this if you want to iterate over all columns


test2(df_2classes)


{0: {0: 2031, 1: 1947, 2: 2001, 3: 2004, 4: 2012}, 1: {0: 1, 1: 0, 2: 0, 3: 0, 4: 2}, 7: {0: 1, 1: 0, 2: 0, 3: 0, 4: 0}, 16: {0: 0, 1: 0, 2: 0, 3: 1, 4: 0}}
{0: {0: 2017, 1: 1947, 2: 1994, 3: 2004, 4: 2000}, 1: {0: 11, 1: 0, 2: 2, 3: 0, 4: 12}, 2: {0: 1, 1: 0, 2: 2, 3: 0, 4: 1}, 3: {0: 1, 1: 0, 2: 3, 3: 0, 4: 1}, 7: {0: 2, 1: 0, 2: 0, 3: 0, 4: 0}, 11: {0: 1, 1: 0, 2: 0, 3: 0, 4: 0}, 16: {0: 0, 1: 0, 2: 0, 3: 1, 4: 0}}
{0: {0: 1895, 1: 1946, 2: 1964, 3: 2003, 4: 1965}, 1: {0: 71, 1: 0, 2: 22, 3: 0, 4: 32}, 2: {0: 38, 1: 0, 2: 8, 3: 0, 4: 7}, 3: {0: 15, 1: 1, 2: 6, 3: 0, 4: 3}, 4: {0: 4, 1: 0, 2: 0, 3: 0, 4: 1}, 5: {0: 3, 1: 0, 2: 0, 3: 1, 4: 1}, 6: {0: 1, 1: 0, 2: 0, 3: 0, 4: 1}, 7: {0: 3, 1: 0, 2: 0, 3: 0, 4: 0}, 8: {0: 1, 1: 0, 2: 0, 3: 0, 4: 0}, 12: {0: 0, 1: 0, 2: 0, 3: 0, 4: 1}, 16: {0: 0, 1: 0, 2: 0, 3: 1, 4: 0}, 25: {0: 0, 1: 0, 2: 0, 3: 0, 4: 1}, 30: {0: 1, 1: 0, 2: 0, 3: 0, 4: 0}, 32: {0: 1, 1: 0, 2: 0, 3: 0, 4: 0}, 34: {0: 0, 1: 0, 2: 0, 3: 0, 4: 1}, 52: {0: 0, 1: 0, 2: 1, 3: 

# work in progress thing

In [ ]:
def column_gini(sliced_data,full_counts):
      # Slice data to include the current column and the last column
      # Group by the first column and count occurrences of each class in the second column
      grouped = sliced_data.groupby(sliced_data.columns[0])[sliced_data.columns[1]].value_counts().unstack(fill_value=0)
      # Ensure only classes 0 to 4 are present and in order
      grouped = grouped.reindex(columns=range(5), fill_value=0)
      # Convert directly to a list of lists
      result_list = grouped.values.tolist()
      values=sorted(sliced_data[sliced_data.columns[0]].unique())
      for value in range(len(values)):
           left_counts=
           print(values[value])
           print(result_list[value])

      


def test2(data):
    full_counts = list(data[784].value_counts())
    for column in range(10):#data.columns[:-1]:
        # Slice data to include the current column and the last column
        sliced_data = data[[column, data.columns[-1]]]
          # Use column label, not index
        result=column_gini(sliced_data,full_counts)
        #print(result)  # Debugging output
        
          # Remove this if you want to iterate over all columns



test2(df_2classes)

0
[2031, 1947, 2001, 2004, 2012]
1
[1, 0, 0, 0, 2]
7
[1, 0, 0, 0, 0]
16
[0, 0, 0, 1, 0]
0
[2017, 1947, 1994, 2004, 2000]
1
[11, 0, 2, 0, 12]
2
[1, 0, 2, 0, 1]
3
[1, 0, 3, 0, 1]
7
[2, 0, 0, 0, 0]
11
[1, 0, 0, 0, 0]
16
[0, 0, 0, 1, 0]
0
[1895, 1946, 1964, 2003, 1965]
1
[71, 0, 22, 0, 32]
2
[38, 0, 8, 0, 7]
3
[15, 1, 6, 0, 3]
4
[4, 0, 0, 0, 1]
5
[3, 0, 0, 1, 1]
6
[1, 0, 0, 0, 1]
7
[3, 0, 0, 0, 0]
8
[1, 0, 0, 0, 0]
12
[0, 0, 0, 0, 1]
16
[0, 0, 0, 1, 0]
25
[0, 0, 0, 0, 1]
30
[1, 0, 0, 0, 0]
32
[1, 0, 0, 0, 0]
34
[0, 0, 0, 0, 1]
52
[0, 0, 1, 0, 0]
54
[0, 0, 0, 0, 1]
0
[1810, 1943, 1899, 2001, 1913]
1
[154, 2, 68, 1, 64]
2
[38, 0, 25, 0, 18]
3
[13, 0, 3, 0, 4]
4
[4, 0, 1, 0, 0]
5
[4, 0, 1, 0, 0]
6
[1, 0, 0, 1, 1]
7
[2, 0, 0, 0, 2]
9
[0, 0, 1, 0, 0]
10
[0, 1, 0, 0, 1]
11
[1, 0, 0, 0, 0]
12
[1, 0, 0, 0, 0]
13
[0, 0, 0, 0, 1]
14
[0, 1, 0, 0, 0]
16
[0, 0, 0, 1, 0]
17
[0, 0, 0, 1, 1]
18
[0, 0, 1, 0, 0]
20
[1, 0, 0, 0, 0]
21
[0, 0, 0, 0, 1]
28
[0, 0, 0, 0, 1]
36
[0, 0, 0, 0, 1]
41
[0, 0, 0, 0, 1]
5

In [259]:
def test2(data):
    result_dict = {}
    for column in data.columns[:-1]:
        # Slice data to include the current column and the last column
        sliced_data = data[[column, data.columns[-1]]]

        # Group by the first column and count occurrences of each class in the second column
        grouped = sliced_data.groupby(sliced_data.columns[0])[sliced_data.columns[1]].value_counts().unstack(fill_value=0)

        # Ensure only classes 0 to 4 are present and in order
        grouped = grouped.reindex(columns=range(5), fill_value=0)

        # Convert directly to a list of lists
        result_list = grouped.values.tolist()

        # Store the result in a dictionary with the column name as the key
        result_dict[column] = result_list

    return result_dict

# Usage
result = test2(df_2classes)
print(result)


{0: [[2031, 1947, 2001, 2004, 2012], [1, 0, 0, 0, 2], [1, 0, 0, 0, 0], [0, 0, 0, 1, 0]], 1: [[2017, 1947, 1994, 2004, 2000], [11, 0, 2, 0, 12], [1, 0, 2, 0, 1], [1, 0, 3, 0, 1], [2, 0, 0, 0, 0], [1, 0, 0, 0, 0], [0, 0, 0, 1, 0]], 2: [[1895, 1946, 1964, 2003, 1965], [71, 0, 22, 0, 32], [38, 0, 8, 0, 7], [15, 1, 6, 0, 3], [4, 0, 0, 0, 1], [3, 0, 0, 1, 1], [1, 0, 0, 0, 1], [3, 0, 0, 0, 0], [1, 0, 0, 0, 0], [0, 0, 0, 0, 1], [0, 0, 0, 1, 0], [0, 0, 0, 0, 1], [1, 0, 0, 0, 0], [1, 0, 0, 0, 0], [0, 0, 0, 0, 1], [0, 0, 1, 0, 0], [0, 0, 0, 0, 1]], 3: [[1810, 1943, 1899, 2001, 1913], [154, 2, 68, 1, 64], [38, 0, 25, 0, 18], [13, 0, 3, 0, 4], [4, 0, 1, 0, 0], [4, 0, 1, 0, 0], [1, 0, 0, 1, 1], [2, 0, 0, 0, 2], [0, 0, 1, 0, 0], [0, 1, 0, 0, 1], [1, 0, 0, 0, 0], [1, 0, 0, 0, 0], [0, 0, 0, 0, 1], [0, 1, 0, 0, 0], [0, 0, 0, 1, 0], [0, 0, 0, 1, 1], [0, 0, 1, 0, 0], [1, 0, 0, 0, 0], [0, 0, 0, 0, 1], [0, 0, 0, 0, 1], [0, 0, 0, 0, 1], [0, 0, 0, 0, 1], [1, 0, 0, 0, 0], [0, 0, 0, 0, 1], [1, 0, 0, 0, 0], [0, 